In [1]:
import pandas as pd
plan = pd.read_csv("5_1_time_plan.csv")
phase = pd.read_csv('2_phase_info.csv')
plan = plan[plan.ID.isin([1, 5, 8, 11])]
ID2starttime = {1:"00:00", 5:"07:00", 8:"09:00", 11:"18:30"}
plan['start_hour'] = plan.ID.apply(lambda id:ID2starttime[id].split(":")[0])
plan['start_minute']=plan.ID.apply(lambda id:ID2starttime[id].split(":")[1])
plan = plan[['inter_no', 'start_hour', 'start_minute', 'phase_no', 'ring_type', 'duration']]
plan = pd.merge(plan, phase[['inter_no', 'phase_no', 'ring_type', 'flow_no']], on=['inter_no', 'phase_no', 'ring_type'], how='left')
plan['flow_no'] = plan['flow_no'].fillna(18).astype(int)
plan[:40]

inter_no start_hour start_minute  phase_no ring_type  duration  flow_no
0        175         00           00         1         A        37        8
1        175         00           00         1         B        37        4
2        175         00           00         2         A        39        7
3        175         00           00         2         B        39        3
4        175         00           00         3         A        55        6
5        175         00           00         3         B        25        1
6        175         00           00         4         A        29        5
7        175         00           00         4         B        59        2
8        175         07           00         1         A        40        8
9        175         07           00         1         B        40        4
10       175         07           00         2         A        42        7
11       175         07           00         2         B        42        3
12       175         07           00         3         A        55        6
13       175         07           00         3         B        29        1
14       175         07           00         4         A        33        5
15       175         07           00         4         B        59        2
16       175         09           00         1         A        43        8
17       175         09           00         1         B        43        4
18       175         09           00         2         A        45        7
19       175         09           00         2         B        45        3
20       175         09           00         3         A        55        6
21       175         09           00         3         B        33        1
22       175         09           00         4         A        37        5
23       175         09           00         4         B        59        2
24       175         18           30         1         A        46        8
25       175         18           30         1         B        46        4
26       175         18           30         2         A        48        7
27       175         18           30         2         B        48        3
28       175         18           30         3         A        55        6
29       175         18           30         3         B        37        1
30       175         18           30         4         A        41        5
31       175         18           30         4         B        59        2
32       176         00           00         1         A        37        8
33       176         00           00         1         B        37        4
34       176         00           00         2         A        73        8
35       176         00           00         2         B        73        3
36       176         00           00         3         A        40        5
37       176         00           00         3         B        40       18
38       176         07           00         1         A        37        8
39       176         07           00         1         B        37        4

In [2]:
# with pd.option_context('display.max_rows', None, 'display.max_columns', None):
#     display(plan)

In [3]:
plans = {index:group for index, group in plan.groupby(['inter_no', 'start_hour', 'start_minute'])}
keys = list(plans.keys())

In [4]:
trans175 = [key[1:3] for key in keys if key[0]==175]
trans175

[('00', '00'), ('07', '00'), ('09', '00'), ('18', '30')]

In [5]:
from datetime import datetime
move = pd.DataFrame()
now = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
for i in range(len(trans175)):
    print(i)
    hhmm = trans175[i]
    df = plans[(175,hhmm[0],hhmm[1])].copy()
    df = df.pivot_table(index=['inter_no', 'start_hour', 'start_minute', 'phase_no'],
                                    columns='ring_type',
                                    values=['duration', 'flow_no'],
                                    aggfunc='first').reset_index()
    df.columns = ['inter_no', 'start_hour', 'start_minute', 'phase_no', 'dura_A', 'dura_B', 'move_A', 'move_B']

    if i < 3:
        hhmm = trans175[i+1]
    else:
        hhmm = (23,59)
    trans = int(datetime(2024, 1, 5, int(hhmm[0]), int(hhmm[1]), 0).timestamp())
    cycle = df.dura_A.sum()
    display(df)
    print(cycle)
    while True:
        A_phas = []
        B_phas = []
        A_move = []
        B_move = []
        for _, row in df.iterrows():
            A_phas += [row['phase_no']] * row['dura_A']
            B_phas += [row['phase_no']] * row['dura_B']
            A_move += [row['move_A']] * row['dura_A']
            B_move += [row['move_B']] * row['dura_B']
        unix_time = range(now, now + cycle)
        inter_no = list(df.inter_no.unique()) * cycle
        move = pd.concat([move, pd.DataFrame({'inter_no':inter_no, 'unix_time':unix_time, 'A_phas':A_phas, 'B_phas':B_phas, 'A_move':A_move, 'B_move':B_move})])
        now += cycle
        if now > trans:
            break
    move

0


inter_no start_hour start_minute  phase_no  dura_A  dura_B  move_A  move_B
0       175         00           00         1      37      37       8       4
1       175         00           00         2      39      39       7       3
2       175         00           00         3      55      25       6       1
3       175         00           00         4      29      59       5       2

160
1


inter_no start_hour start_minute  phase_no  dura_A  dura_B  move_A  move_B
0       175         07           00         1      40      40       8       4
1       175         07           00         2      42      42       7       3
2       175         07           00         3      55      29       6       1
3       175         07           00         4      33      59       5       2

170
2


inter_no start_hour start_minute  phase_no  dura_A  dura_B  move_A  move_B
0       175         09           00         1      43      43       8       4
1       175         09           00         2      45      45       7       3
2       175         09           00         3      55      33       6       1
3       175         09           00         4      37      59       5       2

180
3


inter_no start_hour start_minute  phase_no  dura_A  dura_B  move_A  move_B
0       175         18           30         1      46      46       8       4
1       175         18           30         2      48      48       7       3
2       175         18           30         3      55      37       6       1
3       175         18           30         4      41      59       5       2

190


In [6]:
len(move)

86380

In [7]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(move[20000:30000])

inter_no   unix_time  A_phas  B_phas  A_move  B_move
0         175  1704400400       1       1       8       4
1         175  1704400401       1       1       8       4
2         175  1704400402       1       1       8       4
3         175  1704400403       1       1       8       4
4         175  1704400404       1       1       8       4
5         175  1704400405       1       1       8       4
6         175  1704400406       1       1       8       4
7         175  1704400407       1       1       8       4
8         175  1704400408       1       1       8       4
9         175  1704400409       1       1       8       4
10        175  1704400410       1       1       8       4
11        175  1704400411       1       1       8       4
12        175  1704400412       1       1       8       4
13        175  1704400413       1       1       8       4
14        175  1704400414       1       1       8       4
15        175  1704400415       1       1       8       4
16        175  1704400416       1       1       8       4
17        175  1704400417       1       1       8       4
18        175  1704400418       1       1       8       4
19        175  1704400419       1       1       8       4
20        175  1704400420       1       1       8       4
21        175  1704400421       1       1       8       4
22        175  1704400422       1       1       8       4
23        175  1704400423       1       1       8       4
24        175  1704400424       1       1       8       4
25        175  1704400425       1       1       8       4
26        175  1704400426       1       1       8       4
27        175  1704400427       1       1       8       4
28        175  1704400428       1       1       8       4
29        175  1704400429       1       1       8       4
30        175  1704400430       1       1       8       4
31        175  1704400431       1       1       8       4
32        175  1704400432       1       1       8       4
33        175  1704400433       1       1       8       4
34        175  1704400434       1       1       8       4
35        175  1704400435       1       1       8       4
36        175  1704400436       1       1       8       4
37        175  1704400437       2       2       7       3
38        175  1704400438       2       2       7       3
39        175  1704400439       2       2       7       3
40        175  1704400440       2       2       7       3
41        175  1704400441       2       2       7       3
42        175  1704400442       2       2       7       3
43        175  1704400443       2       2       7       3
44        175  1704400444       2       2       7       3
45        175  1704400445       2       2       7       3
46        175  1704400446       2       2       7       3
47        175  1704400447       2       2       7       3
48        175  1704400448       2       2       7       3
49        175  1704400449       2       2       7       3
50        175  1704400450       2       2       7       3
51        175  1704400451       2       2       7       3
52        175  1704400452       2       2       7       3
53        175  1704400453       2       2       7       3
54        175  1704400454       2       2       7       3
55        175  1704400455       2       2       7       3
56        175  1704400456       2       2       7       3
57        175  1704400457       2       2       7       3
58        175  1704400458       2       2       7       3
59        175  1704400459       2       2       7       3
60        175  1704400460       2       2       7       3
61        175  1704400461       2       2       7       3
62        175  1704400462       2       2       7       3
63        175  1704400463       2       2       7       3
64        175  1704400464       2       2       7       3
65        175  1704400465       2       2       7       3
66        175  1704400466       2       2       7       3
67        175  1704400467       2       2       7       3
68 

In [12]:
datetime.fromtimestamp(1704410399)

datetime.datetime(2024, 1, 5, 8, 19, 59)

In [9]:
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
print(midnight + 7*60*60)

1704405600


In [10]:
move.unix_time.max()
datetime.fromtimestamp(move.unix_time.max())

datetime.datetime(2024, 1, 5, 23, 59, 39)

In [11]:
from datetime import datetime
move_cols = ['inter_no', 'unix_time', 'A_phas', 'B_phas', 'A_move', 'B_move']
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
move = pd.DataFrame(columns = move_cols)
for i in range(37):
    move.loc[i] = pd.Series(dict(zip(move_cols,[175, midnight+i, 1, 1, 8, 4])))
for i in range(37,37+39):
    move.loc[i] = pd.Series(dict(zip(move_cols,[175, midnight+37+i, 2, 2, 7, 3])))
move[:60]

inter_no   unix_time  A_phas  B_phas  A_move  B_move
0        175  1704380400       1       1       8       4
1        175  1704380401       1       1       8       4
2        175  1704380402       1       1       8       4
3        175  1704380403       1       1       8       4
4        175  1704380404       1       1       8       4
5        175  1704380405       1       1       8       4
6        175  1704380406       1       1       8       4
7        175  1704380407       1       1       8       4
8        175  1704380408       1       1       8       4
9        175  1704380409       1       1       8       4
10       175  1704380410       1       1       8       4
11       175  1704380411       1       1       8       4
12       175  1704380412       1       1       8       4
13       175  1704380413       1       1       8       4
14       175  1704380414       1       1       8       4
15       175  1704380415       1       1       8       4
16       175  1704380416       1       1       8       4
17       175  1704380417       1       1       8       4
18       175  1704380418       1       1       8       4
19       175  1704380419       1       1       8       4
20       175  1704380420       1       1       8       4
21       175  1704380421       1       1       8       4
22       175  1704380422       1       1       8       4
23       175  1704380423       1       1       8       4
24       175  1704380424       1       1       8       4
25       175  1704380425       1       1       8       4
26       175  1704380426       1       1       8       4
27       175  1704380427       1       1       8       4
28       175  1704380428       1       1       8       4
29       175  1704380429       1       1       8       4
30       175  1704380430       1       1       8       4
31       175  1704380431       1       1       8       4
32       175  1704380432       1       1       8       4
33       175  1704380433       1       1       8       4
34       175  1704380434       1       1       8       4
35       175  1704380435       1       1       8       4
36       175  1704380436       1       1       8       4
37       175  1704380474       2       2       7       3
38       175  1704380475       2       2       7       3
39       175  1704380476       2       2       7       3
40       175  1704380477       2       2       7       3
41       175  1704380478       2       2       7       3
42       175  1704380479       2       2       7       3
43       175  1704380480       2       2       7       3
44       175  1704380481       2       2       7       3
45       175  1704380482       2       2       7       3
46       175  1704380483       2       2       7       3
47       175  1704380484       2       2       7       3
48       175  1704380485       2       2       7       3
49       175  1704380486       2       2       7       3
50       175  1704380487       2       2       7       3
51       175  1704380488       2       2       7       3
52       175  1704380489       2       2       7       3
53       175  1704380490       2       2       7       3
54       175  1704380491       2       2       7       3
55       175  1704380492       2       2       7       3
56       175  1704380493       2       2       7       3
57       175  1704380494       2       2       7       3
58       175  1704380495       2       2       7       3
59       175  1704380496       2       2       7       3